# **02443 - Computer Exercise 3: Sampling from Continuous Distributions**

In [211]:
import numpy as np
import pandas as pd
from scipy.stats import t, chi2

import plotly.graph_objects as go
import plotly.express as px
import plotly.subplots as sp
import plotly.io as pio
pio.renderers.default = "notebook+pdf"
pio.templates.default = "plotly_dark"

## **Part 1 - Generating simulated values**

**Functions for transforming uniform random variables to other distributions**

In [212]:
def exp_pdf(x, y=1):
    return y*np.exp(-y*x)

def pareto_pdf(x, k=20, beta=1):
    return k*beta**k / x**(k+1)

def gaussian_pdf(x, mu=0, sigma=1):
    return 1/np.sqrt(2*np.pi)*np.exp(-((x-mu)**2)/(2*sigma**2))

def uniform_2_exponential(U, y=1):
    X = -np.log(U)/y
    return X

def uniform_2_pareto(U, k=20, beta=1):
    X = beta*(U**(-1/k))
    return X

def uniform_2_normal(U):
    n = len(U)
    U1, U2 = U[:int(n/2)], U[int(n/2):]
    theta = 2*np.pi*U2
    r = np.sqrt(-2*np.log(U1))
    Z1, Z2 = r*np.array([np.cos(theta), np.sin(theta)])
    return np.concatenate((Z1, Z2))

**Generate random numbers from exponential, pareto and normal distributions**

In [213]:
U = np.random.rand(10000)

X_exp = uniform_2_exponential(U)
X_pareto = uniform_2_pareto(U, beta=1)
X_norm = uniform_2_normal(U)

**Plot histograms of the generated random numbers with superimposed pdf**

In [214]:
# Plot
num_bins = 30
fig = sp.make_subplots(rows=1, cols=3, subplot_titles=("Exponential distribution", "Pareto distribution", "Normal distribution"))

x_exp = np.linspace(min(X_exp), max(X_exp), 100, endpoint=True)
fig.add_trace(go.Scatter(x=x_exp, y=exp_pdf(x_exp), mode='lines', name='PDF', line=dict(color='red')), row=1, col=1)
fig.add_trace(go.Histogram(x=X_exp, xbins=dict(start=0, size=(x_exp[-1]-x_exp[0])/num_bins), histnorm='probability density', name='Samples', marker=dict(color='orange'), showlegend=False), row=1, col=1)

x_pareto = np.linspace(min(X_pareto), max(X_pareto), 100, endpoint=True)
fig.add_trace(go.Scatter(x=x_pareto, y=pareto_pdf(x_pareto), mode='lines', name='PDF', line=dict(color='red'), showlegend=False), row=1, col=2)
fig.add_trace(go.Histogram(x=X_pareto, xbins=dict(start=1, size=(x_pareto[-1]-x_pareto[0])/num_bins), histnorm='probability density', name='Samples', marker=dict(color='blue'), showlegend=False), row=1, col=2)

x_norm = np.linspace(min(X_norm), max(X_norm), 100, endpoint=True)
fig.add_trace(go.Scatter(x=x_norm, y=gaussian_pdf(x_norm), mode='lines', name='PDF', line=dict(color='red'), showlegend=False), row=1, col=3)
fig.add_trace(go.Histogram(x=X_norm, xbins=dict(size=(x_norm[-1]-x_norm[0])/num_bins), histnorm='probability density', name='Samples', marker=dict(color='green'), showlegend=False), row=1, col=3)

fig.update_layout(height=300, width=1000, showlegend=True, bargap=0.1, margin=dict(l=50, r=50, t=50, b=50))

In [215]:
beta = 1
ks = np.array([2.05, 2.5, 3, 4])
U = np.random.rand(10000)

# plot using plotly for each of the ks
fig = sp.make_subplots(rows=1, cols=4, subplot_titles=[r"$k = {}$".format(k) for k in ks])
for i, k in enumerate(ks):
    X = uniform_2_pareto(U, k, beta)
    x = np.linspace(min(X), max(X), 100, endpoint=True)
    fig.add_trace(go.Scatter(x=x, y=pareto_pdf(x, k, beta), mode='lines', name='Pareto PDF', line=dict(color='red')), row=1, col=i+1)
    fig.add_trace(go.Histogram(x=X, xbins=dict(start=1, size=(max(X)-min(X))/20), histnorm='probability density', name='Pareto Histogram', marker=dict(color='blue')), row=1, col=i+1)
    fig.update_yaxes(range=[0, 0.35*2**i], row=1, col=i+1)


fig.update_layout(height=350, width=1000, showlegend=False, bargap=0.1, margin=dict(l=50, r=50, t=80, b=50), title="Pareto distribution for different values of $k$")
fig.show()

## **Part 2 - Comparison of simulation and analytic results for Pareto distribution**

In [216]:
nk = 100
nbeta = 100

ks = np.linspace(2.05, 4, nk)
betas = np.linspace(0.05, 10, nbeta)

mean_diff = np.zeros((nk, nbeta))
var_diff = np.zeros((nk, nbeta))
E = np.zeros((nk, nbeta))
V = np.zeros((nk, nbeta))

U = np.random.rand(10000)

for i, k in enumerate(ks):
    for j, beta in enumerate(betas):
        X = uniform_2_pareto(U, k, beta)
        EX = beta*k/(k-1)
        VarX = beta**2 * k / ((k-1)**2 * (k-2))
        mean_diff[j, i] = abs(np.mean(X) - EX)
        var_diff[j, i] = abs(np.var(X) - VarX)

fig = sp.make_subplots(rows=1, cols=2, subplot_titles=["Absolute difference in means", "Absolute difference in variance"], horizontal_spacing=0.2)
fig.add_trace(go.Heatmap(z=mean_diff, colorscale='hot', zsmooth='best', colorbar_x=0.42), row=1, col=1)
fig.add_trace(go.Heatmap(z=var_diff, colorscale='hot', zsmooth='best'), row=1, col=2)
fig.update_xaxes(title_text=r"$k$", tickvals=np.arange(0, nk, 20), ticktext=np.round(ks[::20], 1), row=1, col=1)
fig.update_yaxes(title_text=r"$\beta$", tickvals=np.arange(0, nbeta, 20), ticktext=np.round(betas[::20]), row=1, col=1)
fig.update_xaxes(title_text=r"$k$", tickvals=np.arange(0, nk, 20), ticktext=np.round(ks[::20], 1), row=1, col=2)
fig.update_yaxes(title_text=r"$\beta$", tickvals=np.arange(0, nbeta, 20), ticktext=np.round(betas[::20]), row=1, col=2)
fig.update_layout(height=500, width=1200, margin=dict(l=50, r=50, t=50, b=50))
fig.show()


As $k$ gets close to 2 it is seen that the difference between the simulated and the analytic variance increases. The analytic variance of the Pareto distribution is undefined for $k \leq 2$, and tends towards $\infty$ as $k$ approaches 2. The simulated variance is calculated as the sample variance of the generated random numbers, and is therefore always finite. This could explain the increased difference between the simulated and the analytic variance as $k$ approaches 2.

## **Part 3 - Confidence intervals of normal distribution**

In [223]:
alpha = 0.05
n_samples = 100
N = 10

# Generate samples
U = np.random.rand(n_samples, N)
X = uniform_2_normal(U)

# Compute confidence intervals
means = X.mean(axis=1)
stds = X.std(axis=1)
CI_means = means[:, None] + t.ppf([1-alpha/2, alpha/2], N-1)[None, :] * stds[:, None]/np.sqrt(N)
CI_vars = (N-1)*stds[:, None]**2 / chi2.ppf([1-alpha/2, alpha/2], N-1)[None, :]

In [224]:
# Sort samples
sort_idx = np.argsort(means)
means = means[sort_idx]
CI_means = CI_means[sort_idx]

sort_idx = np.argsort(stds)
stds = stds[sort_idx]
CI_vars = CI_vars[sort_idx]

# Plot
fig = sp.make_subplots(rows=1, cols=2)

# Mean
for i, CI in enumerate(CI_means):
    fig.add_trace(go.Scatter(x=CI, y=2*[(i+1)/n_samples], mode='lines', line=dict(color='blue')), row=1, col=1)
fig.add_trace(go.Scatter(x=means, y=np.linspace(1, n_samples, n_samples, endpoint=True)/n_samples, mode='lines', line=dict(color='red')), row=1, col=1)

# Variance
for i, CI in enumerate(CI_vars):
    fig.add_trace(go.Scatter(x=CI, y=2*[(i+1)/n_samples], mode='lines', line=dict(color='blue')), row=1, col=2)
fig.add_trace(go.Scatter(x=stds**2, y=np.linspace(1, n_samples, n_samples, endpoint=True)/n_samples, mode='lines', line=dict(color='red')), row=1, col=2)

# Update the layout
fig.update_layout(height=400, width=800, title_text=r"95\% confidence intervals of 100 samples with 10 observations", showlegend=False)
fig.update_xaxes(title_text="Mean", row=1, col=1); fig.update_xaxes(title_text="Variance", row=1, col=2)
fig.show()

With only 10 simulated observations in each sample, the uncertainty in the estimated mean and variance is large, reflected in the large confidence intervals.

## **Part 4 - Pareto distribution using composition**

In [219]:
num_samples = 10000

# Generate samples from uniform distribution
U1 = np.random.rand(num_samples)
U2 = np.random.rand(num_samples)

# Transform to Pareto distribution using composition method
beta = 1
y_comp = uniform_2_exponential(U1, beta)
X_comp = uniform_2_exponential(U2, y_comp)

# Plot
X_comp_q99 = X_comp[X_comp < np.quantile(X_comp, 0.975)] # Exclude extreme values for plotting purposes
x_pareto = np.linspace(min(X_comp_q99), max(X_comp_q99), 100, endpoint=True) # PDF points
fig = go.Figure(go.Histogram(x=X_comp_q99, xbins=dict(start=1, size=(max(X_comp_q99)-min(X_comp_q99))/20), histnorm='probability density', name='# Samples', marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=x_pareto, y=pareto_pdf(x_pareto, 1, beta), mode='lines', name='Pareto PDF', line=dict(color='red')))
fig.update_layout(height=400, width=800, title_text="Pareto samples using composition", bargap=0.1, margin=dict(l=50, r=50, t=100, b=50))
fig.update_xaxes(range=[1, None]); fig.update_yaxes(range=[0, 0.3])
fig.show()